In [1]:
# ============================================================================
# Greenblatt's Magic Formula Implementation
# Author - Jie Situ
# =============================================================================


import requests
from bs4 import BeautifulSoup
import pandas as pd

In [2]:
tickers = ["AXP","AAPL","BA","CAT","CVX","CSCO","DIS","DOW", "XOM",
           "HD","IBM","INTC","JNJ","KO","MCD","MMM","MRK","MSFT",
           "NKE","PFE","PG","TRV","UTX","UNH","VZ","V","WMT","WBA"]

#list of tickers whose financial data needs to be extracted
financial_dir = {}

In [3]:
for ticker in tickers:
    try:
    #getting balance sheet data from yahoo finance for the given ticker
        temp_dir = {}
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/balance-sheet?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[1]
        
        #getting income statement data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/financials?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[2]
        
        #getting cashflow statement data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/cash-flow?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        tabl = soup.find_all("div", {"class" : "M(0) Whs(n) BdEnd Bdc($seperatorColor) D(itb)"})
        for t in tabl:
            rows = t.find_all("div", {"class" : "rw-expnded"})
            for row in rows:
                temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[2]
        
        #getting key statistics data from yahoo finance for the given ticker
        url = 'https://in.finance.yahoo.com/quote/'+ticker+'/key-statistics?p='+ticker
        page = requests.get(url)
        page_content = page.content
        soup = BeautifulSoup(page_content,'html.parser')
        #tabl = soup.findAll("table", {"class": "W(100%) Bdcl(c) "}) 
        tabl=soup.findAll("table")
        for t in tabl:
            rows = t.find_all("tr")
            for row in rows:
                if len(row.get_text(separator='|').split("|")[0:2])>0:
                    temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[-1]    
        
        #combining all extracted information with the corresponding ticker
        financial_dir[ticker] = temp_dir
    except:
        print("Problem scraping data for ",ticker)


In [4]:
financial_dir['AAPL']

{'Assets': 'Current assets',
 'Current assets': 'Cash',
 'Cash': 'Cash and cash equivalents',
 'Cash and cash equivalents': '3,80,16,000',
 'Other short-term investments': '5,29,27,000',
 'Total cash': '90.94B',
 'Net receivables': '1,61,20,000',
 'Inventory': '-1,27,000',
 'Other current assets': '1,12,64,000',
 'Total current assets': '14,37,13,000',
 'Non-current assets': 'Property, plant and equipment',
 'Property, plant and equipment': 'Gross property, plant and equipment',
 'Gross property, plant and equipment': '10,35,26,000',
 'Accumulated depreciation': '-6,67,60,000',
 'Net property, plant and equipment': '3,67,66,000',
 'Equity and other investments': '10,08,87,000',
 'Goodwill': '-',
 'Intangible assets': '-',
 'Other long-term assets': '4,25,22,000',
 'Total non-current assets': '18,01,75,000',
 'Total assets': '32,38,88,000',
 "Liabilities and stockholders' equity": 'Liabilities',
 'Liabilities': 'Current liabilities',
 'Current liabilities': 'Current debt',
 'Current deb

In [5]:
#storing information in pandas dataframe
combined_financials = pd.DataFrame(financial_dir)
combined_financials.dropna(how='all',axis=1,inplace=True) #dropping columns with all NaN values
tickers = combined_financials.columns #updating the tickers list based on only those tickers whose values were successfully extracted


In [6]:
tickers

Index(['AXP', 'AAPL', 'BA', 'CAT', 'CVX', 'CSCO', 'DIS', 'DOW', 'XOM', 'HD',
       'IBM', 'INTC', 'JNJ', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PFE',
       'PG', 'TRV', 'UTX', 'UNH', 'VZ', 'V', 'WMT', 'WBA'],
      dtype='object')

In [7]:
for ticker in tickers:
    combined_financials = combined_financials[~combined_financials[ticker].str.contains("[a-z]").fillna(False)]

combined_financials

AXP          AAPL  \
Total assets                            19,83,21,000  32,38,88,000   
Total liabilities                       17,52,50,000  25,85,49,000   
Common stock                                1,63,000   5,07,79,000   
Retained earnings                        1,38,71,000   1,49,66,000   
Accumulated other comprehensive income    -27,37,000     -4,06,000   
...                                              ...           ...   
PUTX                                             NaN           NaN   
UTX                                              NaN           NaN   
AUTX                                             NaN           NaN   
URTX                                             NaN           NaN   
UTC                                              NaN           NaN   

                                                  BA          CAT  \
Total assets                            13,36,25,000  7,84,53,000   
Total liabilities                       14,19,25,000  6,38,24,000   
Common stock                               50,61,000    59,35,000   
Retained earnings                        5,06,44,000  3,44,37,000   
Accumulated other comprehensive income  -1,61,53,000   -15,67,000   
...                                              ...          ...   
PUTX                                             NaN          NaN   
UTX                                              NaN          NaN   
AUTX                                             NaN          NaN   
URTX                                             NaN          NaN   
UTC                                              NaN          NaN   

                                                 CVX         CSCO  \
Total assets                            23,74,28,000  9,48,53,000   
Total liabilities                        9,22,20,000  5,69,33,000   
Common stock                               18,32,000  4,12,02,000   
Retained earnings                       17,49,45,000   -27,63,000   
Accumulated other comprehensive income    -52,30,000    -5,19,000   
...                                              ...          ...   
PUTX                                             NaN          NaN   
UTX                                              NaN          NaN   
AUTX                                             NaN          NaN   
URTX                                             NaN          NaN   
UTC                                              NaN          NaN   

                                                 DIS           DOW  \
Total assets                            20,15,49,000   6,05,24,000   
Total liabilities                       11,32,86,000   4,64,30,000   
Common stock                             5,44,97,000         8,000   
Retained earnings                        3,83,15,000   1,70,45,000   
Accumulated other comprehensive income    -83,22,000  -1,02,46,000   
...                                              ...           ...   
PUTX                                             NaN           NaN   
UTX                                              NaN           NaN   
AUTX                                             NaN           NaN   
URTX                                             NaN           NaN   
UTC                                              NaN           NaN   

                                                 XOM           HD  ...  \
Total assets                            36,25,97,000  5,12,36,000  ...   
Total liabilities                       16,36,59,000  5,43,52,000  ...   
Common stock                             1,56,37,000       89,000  ...   
Retained earnings                       42,13,41,000  5,17,29,000  ...   
Accumulated other comprehensive income  -1,94,93,000    -7,39,000  ...   
...                                              ...          ...  ...   
PUTX                                             NaN          NaN  ...   
UTX                                              NaN          NaN  ...   
AUTX                                       

In [8]:
# creating dataframe with relevant financial information for each stock using fundamental data
stats = ["EBITDA",
         "Depreciation & amortisation",
         "Market cap (intra-day)",
         "Net income available to common shareholders",
         "Net cash provided by operating activities",
         "Capital expenditure",
         "Total current assets",
         "Total current liabilities",
         "Net property, plant and equipment",
         "Total stockholders' equity",
         "Long-term debt",
         "Forward annual dividend yield"] # change as required

indx = ["EBITDA","D&A","MarketCap","NetIncome","CashFlowOps","Capex","CurrAsset",
        "CurrLiab","PPE","BookValue","TotDebt","DivYield"]
all_stats = {}


In [9]:
temp=combined_financials['AAPL']
temp

Total assets                              32,38,88,000
Total liabilities                         25,85,49,000
Common stock                               5,07,79,000
Retained earnings                          1,49,66,000
Accumulated other comprehensive income       -4,06,000
                                              ...     
PUTX                                               NaN
UTX                                                NaN
AUTX                                               NaN
URTX                                               NaN
UTC                                                NaN
Name: AAPL, Length: 155, dtype: object

In [10]:
ticker_stats=[]
ticker_stats.append(temp.loc['EBITDA'])
ticker_stats

['77.34B']

In [11]:
for ticker in tickers:
    temp = combined_financials[ticker]
    ticker_stats = []
    for stat in stats:
        ticker_stats.append(temp.loc[stat])
    all_stats[ticker] = ticker_stats


In [12]:
all_stats

{'AXP': ['N/A',
  '11,88,000',
  '98.06B',
  '66,31,000',
  '1,36,32,000',
  '-16,45,000',
  nan,
  nan,
  nan,
  '2,30,71,000',
  nan,
  '1.41%'],
 'AAPL': ['77.34B',
  '1,10,56,000',
  '2.22T',
  '5,74,11,000',
  '8,06,74,000',
  '-73,09,000',
  '14,37,13,000',
  '10,53,92,000',
  '3,67,66,000',
  '6,53,39,000',
  '9,86,67,000',
  '0.63%'],
 'BA': ['-2.21B',
  '22,71,000',
  '118.49B',
  '-6,36,000',
  '-24,46,000',
  '-19,61,000',
  '10,22,29,000',
  '9,73,12,000',
  '1,25,02,000',
  '-86,17,000',
  '1,98,04,000',
  'N/A'],
 'CAT': ['7.49B',
  '25,77,000',
  '105.53B',
  '60,93,000',
  '69,12,000',
  '-26,69,000',
  '3,91,93,000',
  '2,66,21,000',
  '1,29,04,000',
  '1,45,88,000',
  '2,61,53,000',
  '2.12%'],
 'CVX': ['15.76B',
  nan,
  '175.33B',
  '29,24,000',
  '2,73,14,000',
  '-1,41,16,000',
  '2,83,29,000',
  '2,65,30,000',
  '15,04,94,000',
  '14,42,13,000',
  '2,36,91,000',
  '5.75%'],
 'CSCO': ['15.22B',
  '18,08,000',
  '190.4B',
  '1,12,14,000',
  '1,54,26,000',
  '-7,70,

In [13]:
# cleansing of fundamental data imported in dataframe
all_stats_df = pd.DataFrame(all_stats,index=indx)
all_stats_df[tickers] = all_stats_df[tickers].replace({',': ''}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'M': 'E+03'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'B': 'E+06'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'T': 'E+09'}, regex=True)
all_stats_df[tickers] = all_stats_df[tickers].replace({'%': 'E-02'}, regex=True)
for ticker in all_stats_df.columns:
    all_stats_df[ticker] = pd.to_numeric(all_stats_df[ticker].values,errors='coerce')
all_stats_df.dropna(axis=1,inplace=True)
tickers = all_stats_df.columns

In [14]:
# calculating relevant financial metrics for each stock
transpose_df = all_stats_df.transpose()
final_stats_df = pd.DataFrame()
final_stats_df["EBIT"] = transpose_df["EBITDA"] - transpose_df["D&A"]
final_stats_df["TEV"] =  transpose_df["MarketCap"].fillna(0) \
                         +transpose_df["TotDebt"].fillna(0) \
                         -(transpose_df["CurrAsset"].fillna(0)-transpose_df["CurrLiab"].fillna(0))
final_stats_df["EarningYield"] =  final_stats_df["EBIT"]/final_stats_df["TEV"]
final_stats_df["FCFYield"] = (transpose_df["CashFlowOps"]-transpose_df["Capex"])/transpose_df["MarketCap"]
final_stats_df["ROC"]  = (transpose_df["EBITDA"] - transpose_df["D&A"])/(transpose_df["PPE"]+transpose_df["CurrAsset"]-transpose_df["CurrLiab"])
final_stats_df["BookToMkt"] = transpose_df["BookValue"]/transpose_df["MarketCap"]
final_stats_df["DivYield"] = transpose_df["DivYield"]

In [15]:
final_stats_df

EBIT           TEV  EarningYield  FCFYield       ROC  BookToMkt  \
AAPL  66284000.0  2.280346e+09      0.029068  0.039632  0.882763   0.029432   
CAT    4913000.0  1.191110e+08      0.041247  0.090789  0.192848   0.138236   
CSCO  13412000.0  1.837360e+08      0.072996  0.085063  0.648079   0.199160   
DOW    2652000.0  5.301900e+07      0.050020  0.182955  0.090809   0.313594   
HD    19634000.0  3.169350e+08      0.061950  0.056614  0.658859  -0.010756   
IBM    9631000.0  1.679130e+08      0.057357  0.154344  0.612503   0.181970   
INTC  26224000.0  2.280390e+08      0.114998  0.233195  0.407743   0.366904   
JNJ   20251000.0  4.384940e+08      0.046183  0.063882  0.750927   0.141157   
KO     9945000.0  2.535880e+08      0.039217  0.057059  2.325772   0.086470   
MCD    7342100.0  1.950312e+08      0.037646  0.065376  0.196533  -0.051043   
MMM    7007000.0  1.098790e+08      0.063770  0.091239  0.502654   0.104703   
MRK   15358000.0  2.275430e+08      0.067495  0.080511  0.755956   0.123326   
MSFT  55324000.0  1.609973e+09      0.034363  0.045853  0.340437   0.071267   
NKE    3971000.0  2.278540e+08      0.017428  0.015478  0.196244   0.034912   
PFE   13310000.0  2.468360e+08      0.053922  0.073563  1.406085   0.305955   
PG    17027000.0  3.726760e+08      0.045688  0.059497  1.084315   0.135177   
UNH   23420000.0  4.007460e+08      0.058441  0.059555 -2.242436   0.167105   
VZ    30848000.0  3.465070e+08      0.089026  0.228209  0.287724   0.256690   
V     14123000.0  4.828760e+08      0.029248  0.023531  0.889806   0.076241   
WMT   27033000.0  4.745580e+08      0.056965  0.086680  0.243398   0.179986   
WBA    2603000.0  6.026000e+07      0.043196  0.175576  0.099854   0.528341   

      DivYield  
AAPL    0.0063  
CAT     0.0212  
CSCO    0.0320  
DOW     0.0479  
HD      0.0224  
IBM     0.0504  
INTC    0.0253  
JNJ     0.0252  
KO      0.0328  
MCD     0.0245  
MMM     0.0346  
MRK     0.0309  
MSFT    0.0103  
NKE     0.0076  
PFE     0.0421  
PG      0.0228  
UNH     0.0137  
VZ      0.0429  
V       0.0060  
WMT     0.0147  
WBA     0.0435

In [16]:
################################Output Dataframes##############################

# finding value stocks based on Magic Formula
final_stats_val_df = final_stats_df.loc[tickers,:]
final_stats_val_df["CombRank"] = final_stats_val_df["EarningYield"].rank(ascending=False,na_option='bottom')+final_stats_val_df["ROC"].rank(ascending=False,na_option='bottom')
final_stats_val_df["MagicFormulaRank"] = final_stats_val_df["CombRank"].rank(method='first')
value_stocks = final_stats_val_df.sort_values("MagicFormulaRank").iloc[:,[2,4,8]]
print("------------------------------------------------")
print("Value stocks based on Greenblatt's Magic Formula")
print(value_stocks)

final_stats_val_df

------------------------------------------------
Value stocks based on Greenblatt's Magic Formula
      EarningYield       ROC  MagicFormulaRank
MRK       0.067495  0.755956               1.0
CSCO      0.072996  0.648079               2.0
PFE       0.053922  1.406085               3.0
INTC      0.114998  0.407743               4.0
HD        0.061950  0.658859               5.0
MMM       0.063770  0.502654               6.0
PG        0.045688  1.084315               7.0
VZ        0.089026  0.287724               8.0
KO        0.039217  2.325772               9.0
IBM       0.057357  0.612503              10.0
JNJ       0.046183  0.750927              11.0
V         0.029248  0.889806              12.0
WMT       0.056965  0.243398              13.0
AAPL      0.029068  0.882763              14.0
UNH       0.058441 -2.242436              15.0
DOW       0.050020  0.090809              16.0
MSFT      0.034363  0.340437              17.0
CAT       0.041247  0.192848              18.0
MCD      

EBIT           TEV  EarningYield  FCFYield       ROC  BookToMkt  \
AAPL  66284000.0  2.280346e+09      0.029068  0.039632  0.882763   0.029432   
CAT    4913000.0  1.191110e+08      0.041247  0.090789  0.192848   0.138236   
CSCO  13412000.0  1.837360e+08      0.072996  0.085063  0.648079   0.199160   
DOW    2652000.0  5.301900e+07      0.050020  0.182955  0.090809   0.313594   
HD    19634000.0  3.169350e+08      0.061950  0.056614  0.658859  -0.010756   
IBM    9631000.0  1.679130e+08      0.057357  0.154344  0.612503   0.181970   
INTC  26224000.0  2.280390e+08      0.114998  0.233195  0.407743   0.366904   
JNJ   20251000.0  4.384940e+08      0.046183  0.063882  0.750927   0.141157   
KO     9945000.0  2.535880e+08      0.039217  0.057059  2.325772   0.086470   
MCD    7342100.0  1.950312e+08      0.037646  0.065376  0.196533  -0.051043   
MMM    7007000.0  1.098790e+08      0.063770  0.091239  0.502654   0.104703   
MRK   15358000.0  2.275430e+08      0.067495  0.080511  0.755956   0.123326   
MSFT  55324000.0  1.609973e+09      0.034363  0.045853  0.340437   0.071267   
NKE    3971000.0  2.278540e+08      0.017428  0.015478  0.196244   0.034912   
PFE   13310000.0  2.468360e+08      0.053922  0.073563  1.406085   0.305955   
PG    17027000.0  3.726760e+08      0.045688  0.059497  1.084315   0.135177   
UNH   23420000.0  4.007460e+08      0.058441  0.059555 -2.242436   0.167105   
VZ    30848000.0  3.465070e+08      0.089026  0.228209  0.287724   0.256690   
V     14123000.0  4.828760e+08      0.029248  0.023531  0.889806   0.076241   
WMT   27033000.0  4.745580e+08      0.056965  0.086680  0.243398   0.179986   
WBA    2603000.0  6.026000e+07      0.043196  0.175576  0.099854   0.528341   

      DivYield  CombRank  MagicFormulaRank  
AAPL    0.0063      25.0              14.0  
CAT     0.0212      33.0              18.0  
CSCO    0.0320      12.0               2.0  
DOW     0.0479      31.0              16.0  
HD      0.0224      14.0               5.0  
IBM     0.0504      18.0              10.0  
INTC    0.0253      13.0               4.0  
JNJ     0.0252      19.0              11.0  
KO      0.0328      17.0               9.0  
MCD     0.0245      33.0              19.0  
MMM     0.0346      16.0               6.0  
MRK     0.0309      10.0               1.0  
MSFT    0.0103      31.0              17.0  
NKE     0.0076      38.0              21.0  
PFE     0.0421      12.0               3.0  
PG      0.0228      16.0               7.0  
UNH     0.0137      28.0              15.0  
VZ      0.0429      16.0               8.0  
V       0.0060      23.0              12.0  
WMT     0.0147      24.0              13.0  
WBA     0.0435      33.0              20.0

In [17]:
# finding highest dividend yield stocks
high_dividend_stocks = final_stats_df.sort_values("DivYield",ascending=False).iloc[:,6]
print("------------------------------------------------")
print("Highest dividend paying stocks")
print(high_dividend_stocks)

------------------------------------------------
Highest dividend paying stocks
IBM     0.0504
DOW     0.0479
WBA     0.0435
VZ      0.0429
PFE     0.0421
MMM     0.0346
KO      0.0328
CSCO    0.0320
MRK     0.0309
INTC    0.0253
JNJ     0.0252
MCD     0.0245
PG      0.0228
HD      0.0224
CAT     0.0212
WMT     0.0147
UNH     0.0137
MSFT    0.0103
NKE     0.0076
AAPL    0.0063
V       0.0060
Name: DivYield, dtype: float64


In [18]:
# # Magic Formula & Dividend yield combined
final_stats_df["CombRank"] = final_stats_df["EarningYield"].rank(ascending=False,method='first') \
                              +final_stats_df["ROC"].rank(ascending=False,method='first')  \
                              +final_stats_df["DivYield"].rank(ascending=False,method='first')
final_stats_df["CombinedRank"] = final_stats_df["CombRank"].rank(method='first')
value_high_div_stocks = final_stats_df.sort_values("CombinedRank").iloc[:,[2,4,6,8]]
print("------------------------------------------------")
print("Magic Formula and Dividend Yield combined")
print(value_high_div_stocks)


------------------------------------------------
Magic Formula and Dividend Yield combined
      EarningYield       ROC  DivYield  CombinedRank
PFE       0.053922  1.406085    0.0421           1.0
IBM       0.057357  0.612503    0.0504           2.0
MRK       0.067495  0.755956    0.0309           3.0
CSCO      0.072996  0.648079    0.0320           4.0
VZ        0.089026  0.287724    0.0429           5.0
MMM       0.063770  0.502654    0.0346           6.0
INTC      0.114998  0.407743    0.0253           7.0
KO        0.039217  2.325772    0.0328           8.0
HD        0.061950  0.658859    0.0224           9.0
PG        0.045688  1.084315    0.0228          10.0
JNJ       0.046183  0.750927    0.0252          11.0
DOW       0.050020  0.090809    0.0479          12.0
WBA       0.043196  0.099854    0.0435          13.0
WMT       0.056965  0.243398    0.0147          14.0
V         0.029248  0.889806    0.0060          15.0
AAPL      0.029068  0.882763    0.0063          16.0
MCD     

In [19]:
url = 'https://in.finance.yahoo.com/quote/AAPL/key-statistics?p=AAPL'
page = requests.get(url)
page_content = page.content
soup = BeautifulSoup(page_content,'html.parser')
#tabl = soup.findAll("table", {"class": "W(100%) Bdcl(c) "}) # 
tabl=soup.findAll("table") 
for t in tabl:
    rows = t.find_all("tr")
    for row in rows:
        if len(row.get_text(separator='|').split("|")[0:2])>0:
            temp_dir[row.get_text(separator='|').split("|")[0]]=row.get_text(separator='|').split("|")[-1]    
        

In [20]:
r=tabl[0].find_all('tr')
r[0].get_text(separator='|').split("|")

['Market cap (intra-day)', ' ', '5', '2.22T']